In [101]:
# -*- coding: utf-8 -*-

# Sergei Bugrov
# 7-10-17
#
# Downloads all available articles from https://www.nytimes.com
#
# usage : python nytimes.py
#
# python version : 3.6.1
import requests, bs4, os, errno, time, datetime, re
from lxml import html

In [11]:
def download_page(url):
    try:
        page = requests.get(url, timeout=10.0)
    except requests.exceptions.Timeout:
        print('Timeout\n')
        return None
    except requests.exceptions.ConnectionError:
        print('ConnectionError\n')
        time.sleep(120)
        return None
    except requests.exceptions.HTTPError:
        print('HTTPError\n')
        return None
    except requests.exceptions.TooManyRedirects:
        print('TooManyRedirects\n')
        return None
    else:
        return page

In [102]:
def download_page(url):
    USERNAME = "xliu@stern.nyu.edu"
    PASSWORD = "project2018"

    LOGIN_URL = "https://myaccount.nytimes.com/auth/login?URI=https%3A%2F%2Fwww.nytimes.com%2F"

    session_requests = requests.session()

    # Get login csrf token
    result = session_requests.get(LOGIN_URL)
    tree = html.fromstring(result.text)
    #print('tree=',tree)
    #print('here',list(set(tree.xpath("//input[@name='authToken']/@value"))))
    #authenticity_token = list(set(tree.xpath("//input[@name='authToken']/@value")))[0]
    authenticity_token = 'H4sIAAAAAAAAAx2MUQ6CMBAF79JvAhQWtstZSAhs19goLaElSNS72'

    # Create payload
    payload = {
        "username": USERNAME , 
        "password": PASSWORD , 
        "csrfmiddlewaretoken": authenticity_token
    }

    # Perform login
    result = session_requests.post(LOGIN_URL, data = payload, headers = dict(referer = LOGIN_URL))
    print('result=',result)

    # Scrape url
    try:
        page = session_requests.get(url, timeout=10.0)
    except requests.exceptions.Timeout:
        print('Timeout\n')
        return None
    except requests.exceptions.ConnectionError:
        print('ConnectionError\n')
        time.sleep(120)
        return None
    except requests.exceptions.HTTPError:
        print('HTTPError\n')
        return None
    except requests.exceptions.TooManyRedirects:
        print('TooManyRedirects\n')
        return None
    else:
        return page

In [103]:
max_attempts = 10

r_unwanted = re.compile('[\n\t\r]')

urls_to_articles = []

if not os.path.exists('articles/'):
    try:
        os.makedirs('articles/')
    except OSError as e:
        if e.errno != errno.EEXIST:
            raise

In [104]:
# STEP 1. BUILD THE LIST OF URLS TO ARTICLES
if not os.path.exists('urls_to_articles.txt'):

    for year in range(2005, 2015):

        catalog_page_by_years = 'http://spiderbites.nytimes.com/%s/' % (year)
        #catalog_page_by_years = 'http://spiderbites.nytimes.com/free_%s/index.html' % (year)

        links_to_parts = []

        attempts = 0

        print('Year: ', year)
        print('catalog_page_by_years=',catalog_page_by_years)

        with open('logfile.log', 'w') as f:
            f.write('STEP 1. Year: ' + str(year) + '\n')

        catalog_page = download_page(catalog_page_by_years)
        print('catalog_page=',catalog_page)
    
        while not (catalog_page or attempts > max_attempts):
            catalog_page = download_page(catalog_page_by_years)
            attempts += 1
        print('attempts=',attempts)
        
        if catalog_page:
            catalog_page = bs4.BeautifulSoup(catalog_page.text, "lxml")
            #if year > 1995:
            #    links_to_parts.append(['http://spiderbites.nytimes.com%s' % (el.get('href')) for el in catalog_page.select('body > div > div > div > div > div > div > ul > li > a')])    
            #else:
            #    links_to_parts.append(['http://spiderbites.nytimes.com/free_%s/%s' % (year, el.get('href')) for el in catalog_page.select('body > div > div > div > div > div > div > ul > li > a')])
                
            #print('here=',catalog_page.select('body > div > div > div > div > ul > li > a')[0].get('href'))
            links_to_parts.append(['http://spiderbites.nytimes.com%s' % (el.get('href')) for el in catalog_page.select('body > div > div > div > div > div > div > ul > li > a')])             
        
        #print('links_to_parts1=',links_to_parts[0])
        links_to_parts = [item for sublist in links_to_parts for item in sublist]
        #print('links_to_parts2=',links_to_parts[0])

        for link_to_parts in links_to_parts:

            attempts = 0
            print('link_to_parts3=',link_to_parts)
            parts_page = download_page(link_to_parts)
            print('parts_page=',parts_page)

            while not (parts_page or attempts > max_attempts):
                parts_page = download_page(link_to_parts)
                attempts += 1

            if parts_page:
                parts_page = bs4.BeautifulSoup(parts_page.text, "lxml")
                #print('parts_page4=',parts_page)
                urls_to_articles.append([el.get('href') for el in parts_page.select('body > div > div > div > div > ul > li > a')])
            
    
    urls_to_articles = [item for sublist in urls_to_articles for item in sublist]
    print('urls_to_articles=',urls_to_articles)

    # Backing up the list of URLs
    with open('urls_to_articles.txt', 'w') as output:
        for u in urls_to_articles:
            output.write('%s\n' % (u.strip()))

Year:  2005
catalog_page_by_years= http://spiderbites.nytimes.com/2005/
result= <Response [200]>
catalog_page= <Response [200]>
attempts= 0
link_to_parts3= http://spiderbites.nytimes.com/2005/articles_2005_01_00000.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2005/articles_2005_01_00001.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2005/articles_2005_01_00002.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2005/articles_2005_01_00003.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2005/articles_2005_01_00004.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2005/articles_2005_01_00005.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2005/arti

result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2005/articles_2005_10_00000.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2005/articles_2005_10_00001.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2005/articles_2005_10_00002.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2005/articles_2005_10_00003.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2005/articles_2005_10_00004.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2005/articles_2005_10_00005.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2005/articles_2005_10_00006.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_

result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2006/articles_2006_07_00002.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2006/articles_2006_07_00003.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2006/articles_2006_08_00000.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2006/articles_2006_08_00001.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2006/articles_2006_08_00002.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2006/articles_2006_08_00003.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2006/articles_2006_09_00000.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_

result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2007/articles_2007_11_00001.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2007/articles_2007_11_00002.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2007/articles_2007_11_00003.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2007/articles_2007_12_00000.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2007/articles_2007_12_00001.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2007/articles_2007_12_00002.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2007/articles_2007_12_00003.html
result= <Response [200]>
parts_page= <Response [200]>
Year:  2

result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2008/articles_2008_11_00002.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2008/articles_2008_11_00003.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2008/articles_2008_11_00004.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2008/articles_2008_12_00000.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2008/articles_2008_12_00001.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2008/articles_2008_12_00002.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2008/articles_2008_12_00003.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_

...

result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2012/articles_2012_02_00000.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2012/articles_2012_02_00001.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2012/articles_2012_02_00002.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2012/articles_2012_02_00003.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2012/articles_2012_02_00004.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2012/articles_2012_02_00005.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2012/articles_2012_02_00006.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_

result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2012/articles_2012_09_00002.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2012/articles_2012_09_00003.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2012/articles_2012_09_00004.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2012/articles_2012_09_00005.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2012/articles_2012_09_00006.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2012/articles_2012_10_00000.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2012/articles_2012_10_00001.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_

result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2013/articles_2013_05_00005.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2013/articles_2013_05_00006.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2013/articles_2013_06_00000.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2013/articles_2013_06_00001.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2013/articles_2013_06_00002.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2013/articles_2013_06_00003.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2013/articles_2013_06_00004.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_

result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2014/articles_2014_03_00003.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2014/articles_2014_03_00004.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2014/articles_2014_03_00005.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2014/articles_2014_03_00006.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2014/articles_2014_04_00000.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2014/articles_2014_04_00001.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_parts3= http://spiderbites.nytimes.com/2014/articles_2014_04_00002.html
result= <Response [200]>
parts_page= <Response [200]>
link_to_

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [ ]:
# STEP 2. DOWNLOAD ARTICLES
# If, at some point, Step 2 is interrupted due to unforeseen
# circumstances (power outage, loss of internet connection), replace the number
# (value of the variable url_num) below with the one you will find in the logfile.log
url_num = 0

if os.path.exists('urls_to_articles.txt') and len(urls_to_articles) == 0:
    with open('urls_to_articles.txt', 'r') as f:
        urls_to_articles = f.read().splitlines()

#print('Number of articles that are about to be downloaded: ', len(urls_to_articles))

for url in urls_to_articles[url_num:]:

    if len(url) > 34:

        attempts = 0

        if url_num % 1000 == 0:

            print('Downloading article #', url_num, ' from ', url)

            with open('logfile.log', 'w') as f:
                f.write('STEP 2. Downloading article #' + str(url_num) + ' from ' + url + '\n')

        article_page = download_page(url)

        while not (article_page or attempts > max_attempts):
            article_page = download_page(url)
            attempts += 1

        if article_page:
            article_page = bs4.BeautifulSoup(article_page.text, "lxml")

            title = [el.getText() for el in article_page.find_all(class_="articleHeadline")]
            if len(title) > 0:
                title = title[0]
            else:
                title = [el.getText() for el in article_page.find_all(class_="headline")]

                if len(title) > 0:
                    title = title[0]
                else:
                    title = ""

            dateline = [el.getText() for el in article_page.find_all(class_="dateline")]
            if len(dateline) > 0:
                dateline = dateline[0]
            else:
                dateline = ""

            byline = [el.getText().strip() for el in article_page.find_all(class_="byline")]
            if len(byline) > 0:
                byline = ' '.join(byline)
            else:
                byline = ""

            body = [el.getText() for el in article_page.find_all(class_="articleBody")]
            if len(body) > 0:
                body = '\n'.join(body)
                body = r_unwanted.sub("", body)
                body = re.sub(' +', ' ', body)

                with open('articles/' + str(url_num) + url.split('/')[-1] + '.txt', 'w') as output:
                    output.write('(c) ' + str(datetime.datetime.now().year) + ' The New York Times Company\n')
                    output.write(url + '\n')
                    output.write(title + '\n')
                    output.write(dateline + '\n')
                    output.write(byline + '\n')
                    output.write('\n' + body)
            else:

                body = [el.getText() for el in article_page.find_all(class_="story-body-text")]

                if len(body) > 0:
                    body = '\n'.join(body)
                    body = r_unwanted.sub("", body)
                    body = re.sub(' +', ' ', body)

                    with open('articles/' + str(dateline)+ str('-')+ str(url_num) + url.split('/')[-1] + '.txt', 'w') as output:
                        output.write('(c) ' + str(datetime.datetime.now().year) + ' The New York Times Company\n')
                        output.write(url + '\n')
                        output.write(title + '\n')
                        output.write(dateline + '\n')
                        output.write(byline + '\n')
                        output.write('\n' + body)
    url_num += 1

result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>


result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>


result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>


result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>


result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>


...

result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>


result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>


result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>


result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>


result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
result= <Response [200]>
